In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import pandas as pd 
import numpy as np
from scipy import stats

import matplotlib.pyplot as plt

This notebook uses the following output files:
1. 'output/Covid_confirm_ranked.csv'
2. 'output/Covid_combo_ranked.csv'

To use compound names:

3. 'data/id_to_names.txt'

In [3]:
single_ranked = pd.read_csv('output/Covid_confirm_ranked.csv', delimiter=';')
combo_ranked = pd.read_csv('output/Covid_combo_ranked.csv', delimiter=';')

# We used the same number of components for Mahalanobis distance in Covid-Confirm and Covid-Combo
N_COMPONENTS = 18

In [4]:
# Use the same name for the 'compound concentration' column
single_ranked.rename(columns={'cmpd_conc': 'conc'}, inplace=True)
combo_ranked.rename(columns={'cmpd_conc': 'conc'}, inplace=True)

# Use the same precision when defining concentrations – 2 decimals
single_ranked = single_ranked.round({'conc': 2})
combo_ranked = combo_ranked.round({'conc': 2})

# Use the same name for the 'median Mahalanobis distance' column
single_ranked.rename(columns={'distance': 'distance_median'}, inplace=True)

In [5]:
# If we want to use batch_id's as compound identifiers
combo_ranked['name'] = combo_ranked['batch_id']
combo_ranked['pair_name'] = combo_ranked['pair_batch_id']

In [6]:
# If we want to use compound names instead of batch_id's
with open("data/id_to_name.txt", 'r') as file:
    table = file.readlines()
id_to_name = {}
for i, line in enumerate(table):
    id_, name = line.rstrip().split('\t')
    id_to_name[id_] = name

def fill_missing_name(batch_id):
    if batch_id in id_to_name:
        return id_to_name[batch_id]
    else:
        return f"Batch_id: {batch_id}"

combo_ranked['name'] = combo_ranked['batch_id'].map(fill_missing_name)
combo_ranked['pair_name'] = combo_ranked['pair_batch_id'].map(fill_missing_name)

In [7]:
def plot_compounds_separately(drugs_single, drugs_combo, negative=None, n_components=None, metric='distance'):

    if n_components is None:
        raise ValueError("Please, specify the number of components used in Mahalanobis distance computation")

    n_decimals_single = max(drugs_single['conc'].astype('str').str.split('.', expand=True)[1].apply(len))
    n_decimals_combo = max(drugs_combo['conc'].astype('str').str.split('.', expand=True)[1].apply(len))

    if n_decimals_single != n_decimals_combo:
        raise ValueError(
            "Need to use the same precision to compare concentrations:" 
            + f"\ndecimals in single drugs = {n_decimals_single},"
            + f"\ndecimals in combinations of drugs = {n_decimals_combo}"
        )

    y_metric = f"{metric}_median"
    y_metric_q_25 = f"{metric}_q_25"
    y_metric_q_75 = f"{metric}_q_75"

    conf_intervals = [0.5, 0.75]
    healthy_left = dict()
    healthy_right = dict()
    for conf in conf_intervals:
        if metric == 'distance':
            left_sq, right_sq = stats.chi2.interval(confidence=conf, df=n_components)
            healthy_left[conf], healthy_right[conf] = np.sqrt(left_sq), np.sqrt(right_sq)        
        elif metric == 'proba':
            healthy_left[conf],  healthy_right[conf] = conf, 1
        
    if negative is not None:
        # neg_median = negative[y_metric].iloc[0]
        neg_left = negative[y_metric].iloc[0] - negative[y_metric_q_25].iloc[0]
        neg_right = negative[y_metric].iloc[0] + negative[y_metric_q_75].iloc[0]

    if metric == 'distance':
        if negative is None:
            ymin, ymax = min(healthy_left.values()), 3*max(healthy_right.values())
        else:
            ymin, ymax = min(healthy_left.values()), neg_right + 1
    elif metric == 'proba':
        ymin, ymax = 0, 1


    batch_ids = drugs_combo['batch_id'].unique()
    cols = 4
    rows = len(batch_ids) // cols
    fig, axs = plt.subplots(rows, cols, figsize=(4*cols, 3*rows))
    fig.tight_layout()

    # Iterate over compounds
    for r in range(rows):
        for c in range(cols):
            i = r * 4 + c
            batch_id = batch_ids[i]

            # Plot this single drug (from Covid-Confirm analysis)
            conc_in_combo = drugs_combo[(drugs_combo['batch_id'] == batch_id)]['conc'].unique()
            compound = drugs_single[(drugs_single['batch_id'] == batch_id) & (drugs_single['conc'].isin(conc_in_combo))]
            sort_arg = np.argsort(compound['conc'])
            conc = compound['conc'].to_numpy()[sort_arg]
            y_values = compound[y_metric].to_numpy()[sort_arg]
            y_perc_25 = compound[y_metric_q_25].to_numpy()[sort_arg]
            y_perc_75 = compound[y_metric_q_75].to_numpy()[sort_arg]
            axs[r, c].errorbar(
                conc, y_values, yerr=[y_perc_25, y_perc_75], 
                capsize=2, elinewidth=1.5, fmt='--', 
                label='single'
            )

            combo_ids = drugs_combo[drugs_combo['batch_id'] == batch_id]['combo_id'].unique()
            drug_concentrations = set()
            # Iterate over and plot combinations containing this drug (from Covid-Combo analysis)
            for combo_id in combo_ids:
                compound = drugs_combo[(drugs_combo['batch_id'] == batch_id) & (drugs_combo['combo_id'] == combo_id)]
                sort_arg = np.argsort(conc_in_combo)
                conc = compound['conc'].to_numpy()[sort_arg]
                y_values = compound[y_metric].to_numpy()[sort_arg]
                y_perc_25 = compound[y_metric_q_25].to_numpy()[sort_arg]
                y_perc_75 = compound[y_metric_q_75].to_numpy()[sort_arg]
                # axs[r, c].plot(
                #     conc, y_values, 
                #     # label=f'combination id: {combo_id}'
                # )
                axs[r, c].errorbar(
                    conc, y_values, yerr=[y_perc_25, y_perc_75], 
                    capsize=2, elinewidth=1.5, #fmt='o-', 
                    label=f'combination id: {combo_id}'
                )
                drug_concentrations = drug_concentrations.union(set(conc))

            x_ticks = list(drug_concentrations)
            
            # Uninfected cells - confidence intervals
            for i, conf in enumerate(conf_intervals):
                label = "Non-infected" if i == 0 else None
                axs[r, c].fill_between(x_ticks, healthy_left[conf], healthy_right[conf], 
                                color='royalblue', alpha=0.5*(1-conf)**0.5, 
                                zorder=1, label=label
                    )
            axs[r, c].text(
                (x_ticks[0]+x_ticks[-1])/2, (healthy_left[conf]+healthy_right[conf])/2, 
                'Non-infected', ha='center', va='center', alpha=0.4
            )
            
            if negative is not None:
                # Negative state (DMSO)
                axs[r, c].fill_between(
                    x_ticks, neg_left, neg_right, 
                    color='k', alpha=0.25, zorder=1,
                )
                axs[r, c].text(
                    (x_ticks[0]+x_ticks[-1])/2, (neg_left+neg_right)/2,
                    'DMSO', ha='center', va='center', alpha=0.4,
                )

            axs[r, c].set_title(compound['name'].iloc[0])
            axs[r, c].set_xticks(x_ticks)
            # axs[r, c].set_xscale('log')
            axs[r, c].set_ylim(ymin, ymax)
            if c == 0:
                axs[r, c].set_ylabel(f'{metric}')
            if r == rows - 1:
                axs[r, c].set_xlabel('concentration')

    fig.savefig(f"output/Covid-single-vs-combo-{metric}.png", dpi=300, bbox_inches="tight")


In [8]:
drugs_single = single_ranked[single_ranked['batch_id'] != 'non-inf'].copy()
drugs_combo = combo_ranked[combo_ranked['type'] == 'treated'].copy()

# negative = combo_ranked[combo_ranked['type'] == 'infected'].copy()
negative = None

In [9]:
plot_compounds_separately(drugs_single, drugs_combo, negative, n_components=N_COMPONENTS)

In [ ]:
plot_compounds_separately(drugs_single, drugs_combo, negative, n_components=N_COMPONENTS, metric='proba')